In [21]:
import sys
sys.path.insert(0, '../nsga-net/')
from search import train_search
import os
import pandas as pd
import plotly.graph_objs as go
import hashlib
import plotly.io as pio
import ast
nas_log_dir = '/home/nima/genologs/search-GA-BiObj-micro-20240425-060906'
import json

In [3]:
def draw_pareto_graph(log_directory):
    accuracy_values = []
    num_parameters_values = []
    file_names = []
    assigned_users = []

    for filename in os.listdir(log_directory):
        if filename.endswith('.csv'):
            filepath = os.path.join(log_directory, filename)
            df = pd.read_csv(filepath, skiprows=lambda x: x % 3 != 0)
            if not df.empty:
                for index, row in df.iterrows():
                    response_list = eval(row['Response'])
                    accuracy_values.append(response_list[0])
                    num_parameters_values.append(response_list[1])
                    file_names.append(filename)
                    assigned_users.append(row.get('Assigned_User', 'N/A'))

    # Check if the lists are empty
    if not num_parameters_values or not accuracy_values:
        # Create an empty plot with a consistent style
        fig = go.Figure()
        fig.add_trace(go.Scatter(x=[], y=[], mode='markers'))
        fig.update_layout(
            title='No data available',
            xaxis=dict(
                title='Number of Parameters',
                title_font=dict(color='#FFFFFF'),
                tickfont=dict(color='#FFFFFF'),
                linecolor='#FFFFFF',
                showgrid=False,
                range=[0, 1]
            ),
            yaxis=dict(
                title='Accuracy',
                title_font=dict(color='#FFFFFF'),
                tickfont=dict(color='#FFFFFF'),
                linecolor='#FFFFFF',
                showgrid=False,
                range=[0, 1]
            ),
            plot_bgcolor='#171B23',
            paper_bgcolor='#171B23',
            legend=dict(font=dict(color='#FFFFFF')),
            hovermode='closest',
            hoverlabel=dict(font=dict(color='#FFFFFF')),
            showlegend=False
        )
        return pio.to_html(fig, full_html=False)

    # Compute unique colors for each file
    unique_colors = [hashlib.sha256(name.encode()).hexdigest()[:6] for name in set(file_names)]

    scatter_traces = []
    for filename, color in zip(set(file_names), unique_colors):
        x_values = [num_parameters_values[i] for i, name in enumerate(file_names) if name == filename]
        y_values = [accuracy_values[i] for i, name in enumerate(file_names) if name == filename]
        hover_text = [f"uid:{assigned_users[i]}" for i, name in enumerate(file_names) if name == filename]
        scatter_trace = go.Scatter(
            x=x_values,
            y=y_values,
            mode='markers',
            name=filename.split('.')[0],
            marker=dict(color=f'#{color}'),
            hoverinfo='text',
            text=hover_text
        )
        scatter_traces.append(scatter_trace)

    pareto_optimal_points = find_pareto_optimal_points(accuracy_values, num_parameters_values)
    print(pareto_optimal_points)
    padding_factor = 0.01  # 10% padding
    x_min, x_max = min(num_parameters_values), max(num_parameters_values)
    y_min, y_max = min(accuracy_values), max(accuracy_values)
    x_range = [(1 - padding_factor) * x_min, (1 + padding_factor) * x_max]
    y_range = [(1 - padding_factor) * y_min, (1 + padding_factor) * y_max]

    fig = go.Figure(data=scatter_traces)
    if pareto_optimal_points:
        pareto_x, pareto_y = zip(*pareto_optimal_points)
        pareto_trace = go.Scatter(
            x=pareto_x,
            y=pareto_y,
            mode='lines',
            name='Pareto Optimal Line',
            line=dict(color='#ff0000')
        )
        fig.add_trace(pareto_trace)

    fig.update_layout(
        title='Scatter Plot of Multi-Objective Optimization Scores',
        xaxis=dict(
            title='Number of Parameters',
            range=x_range,
            title_font=dict(color='#FFFFFF'),
            tickfont=dict(color='#FFFFFF'),
            linecolor='#FFFFFF',
            showgrid=False
        ),
        yaxis=dict(
            title='Accuracy',
            range=y_range,
            title_font=dict(color='#FFFFFF'),
            tickfont=dict(color='#FFFFFF'),
            linecolor='#FFFFFF',
            showgrid=False
        ),
        plot_bgcolor='#171B23',
        paper_bgcolor='#171B23',
        legend=dict(font=dict(color='#FFFFFF')),
        hovermode='closest',
        hoverlabel=dict(font=dict(color='#FFFFFF')),
        showlegend=False
    )

    return fig

def find_pareto_optimal_points(accuracy, parameters):
    pareto_optimal = []
    for i in range(len(accuracy)):
        is_pareto = True
        for j in range(len(accuracy)):
            if accuracy[i] <= accuracy[j] and parameters[i] >= parameters[j] and i != j:
                is_pareto = False
                break
        if is_pareto:
            pareto_optimal.append((parameters[i], accuracy[i]))
    pareto_optimal.sort()
    return pareto_optimal

In [14]:
import pandas as pd
import os
import hashlib
import plotly.graph_objs as go
import plotly.io as pio

def print_pareto(log_directory):
    accuracy_values = []
    num_parameters_values = []
    file_names = []
    assigned_users = []
    genome_values = []  # Store Genome values

    for filename in os.listdir(log_directory):
        if filename.endswith('.csv'):
            filepath = os.path.join(log_directory, filename)
            df = pd.read_csv(filepath, skiprows=lambda x: x % 3 != 0)
            for index, row in df.iterrows():
                response_list = eval(row['Response'])
                accuracy_values.append(response_list[0])
                num_parameters_values.append(response_list[1])
                file_names.append(filename)
                assigned_users.append(row.get('Assigned_User', 'N/A'))
                genome_values.append(row['Genome'])  # Collect Genome values

    # Identify Pareto optimal points
    pareto_indices = find_pareto(accuracy_values, num_parameters_values)

    return pareto_indices, genome_values, assigned_users

def find_pareto(accuracy, parameters):
    pareto_optimal_indices = []
    for i in range(len(accuracy)):
        is_pareto = True
        for j in range(len(accuracy)):
            if accuracy[i] <= accuracy[j] and parameters[i] >= parameters[j] and i != j:
                is_pareto = False
                break
        if is_pareto:
            pareto_optimal_indices.append(i)
    return pareto_optimal_indices

pareto_indices, genome_values, assigned_users = print_pareto(nas_log_dir)
# This is selcted from the Pareto Optimal Line from the figure below
which_genome = 4
for i in range(len(pareto_indices)):
    if assigned_users[pareto_indices[i]] == which_genome:
            genome_string_str = genome_values[pareto_indices[i]]
            genome_string = ast.literal_eval(genome_string_str)
            print(genome_string)
    



[[0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 0, 1, 1, 0, 1, 0, 0], [0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1], [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1]]


In [13]:
fig = draw_pareto_graph(nas_log_dir)
fig.show()

[(0.319366, 89.16), (0.332326, 89.27), (0.336286, 89.34), (0.337582, 89.38), (0.338878, 89.52), (0.342766, 89.62), (0.345358, 89.69), (0.366166, 89.83), (0.375238, 89.87), (0.384382, 89.9), (0.39475, 89.92), (0.399934, 90.31), (0.486982, 90.35), (0.493534, 90.5), (0.542926, 90.62), (0.56755, 90.74), (0.583102, 90.9), (0.58699, 91.19), (0.755758, 91.23), (0.770734, 91.28), (0.824014, 91.32), (0.833086, 91.38), (0.843454, 91.5), (0.88507, 91.57), (0.953902, 91.58), (0.95635, 91.62), (0.977374, 91.63), (1.019998, 91.96), (1.06291, 92.04), (1.196686, 92.09), (1.290142, 92.2), (1.331614, 92.26), (1.38619, 92.29), (1.486126, 92.32), (1.490158, 92.34), (1.54459, 92.46), (1.549774, 92.5), (1.679518, 92.58), (1.91179, 92.63), (2.10403, 92.73), (2.36611, 92.81), (2.674846, 92.83), (2.765566, 92.94)]


In [22]:

results = []
for i in range(len(pareto_indices)):
    print(assigned_users[pareto_indices[i]])
    genome_string_str = genome_values[pareto_indices[i]]
    genome_string = ast.literal_eval(genome_string_str)
    performance = train_search.main(genome=genome_string,
                                            search_space = 'macro',
                                            init_channels = 36,
                                            layers=15, cutout=True,
                                            epochs=350,
                                            save='arch_{}'.format(1),
                                            expr_root='')
    performance['uid']= assigned_users[pareto_indices[i]]
    results.append(performance)
# Write JSON data
with open('result.json', 'w') as file:
    json.dump(performance, file, indent=4)

97
Experiment dir : arch_1
05/02 02:50:44 AM Architecture = [[[0], [1, 0], [0, 1, 0], [1, 1, 0, 1], [1, 0, 0, 0, 0], [0, 1, 0, 0, 1, 0], [1, 0, 1, 0, 0, 0, 0], [0, 1, 0, 0, 1, 0, 0, 0], [0, 0, 1, 0, 0, 0, 0, 1, 0], [0]], [[0], [1, 1], [1, 1, 1], [0, 1, 1, 1], [0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0], [0, 1, 0, 0, 0, 0, 0], [1, 0, 0, 0, 1, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0, 1], [1]], [[0], [0, 0], [0, 0, 0], [0, 0, 0, 0], [0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0, 0], [0]]]
05/02 02:50:44 AM param size = 0.583102MB
2024-05-02 02:50:45.087 |       INFO       | 👷 epoch 0 lr 0.0249989929144142
2024-05-02 02:51:00.106 |       INFO       | 👷 train_acc 38.54             
2024-05-02 02:51:00.107 |       INFO       | 👷 epoch 1 lr 0.024996475337369265
2024-05-02 02:51:15.158 |       INFO       | 👷 train_acc 54.935            
2024-05-02 02:51:15.159 |       INFO       | 👷 epoch 2 lr 0.024992951029702327
2024-05-02 02:51:30.360 |     

In [26]:
import plotly.graph_objs as go

data = results

# Choose the parameter to use for sorting (params or flops)
sort_key = 'flops'

# Sort the data based on the chosen parameter
sorted_data = sorted(data, key=lambda x: x[sort_key])

# Extract x and y values
x_values = [entry[sort_key] for entry in sorted_data]
y_values = [entry['valid_acc'] for entry in sorted_data]
uid_values = [entry['uid'] for entry in sorted_data]

# Create the scatter plot
fig = go.Figure()

fig.add_trace(go.Scatter(x=x_values, y=y_values, mode='markers', text=uid_values,
                          marker=dict(size=10),
                          hoverinfo='x+y+text', name='Validation Accuracy'))

# Add axis labels and title
if sort_key == 'params':
    fig.update_layout(xaxis_title='Parameters', yaxis_title='Validation Accuracy', title='Validation Accuracy vs Parameters')
else:
    fig.update_layout(xaxis_title='FLOPS', yaxis_title='Validation Accuracy', title='Validation Accuracy vs FLOPS')

# Set dark theme
fig.update_layout(template='plotly_dark')

# Show plot
fig.show()

: 

In [20]:
import re
import pandas as pd

# Specify the path to your log file
file_path = 'res.txt'


# Read the log data from the file
with open(file_path, 'r') as file:
    log_data = file.readlines()

# Initialize lists to hold the extracted values
param_sizes = []
valid_accuracies = []
flops_list = []

# Regex patterns to extract the needed information
param_size_pattern = re.compile(r'param size = ([\d\.]+)MB')
valid_acc_pattern = re.compile(r'valid_acc\s+([\d\.]+)')
flops_pattern = re.compile(r'flops = ([\d\.]+)')

# Extract values from the log data
for line in log_data:
    param_size_match = param_size_pattern.search(line)
    valid_acc_match = valid_acc_pattern.search(line)
    flops_match = flops_pattern.search(line)
    
    if param_size_match:
        # print(f"Param Size found: {param_size_match.group(1)}MB")
        param_sizes.append(param_size_match.group(1))
    if valid_acc_match:
        # print(f"Valid Accuracy found: {valid_acc_match.group(1)}")
        valid_accuracies.append(valid_acc_match.group(1))
    if flops_match:
        # print(f"FLOPS found: {flops_match.group(1)}")
        flops_list.append(flops_match.group(1))

        
        
        


print(len(param_sizes))
print(len(valid_accuracies))
print(len(flops_list))
res = []
for i in range(len(param_sizes)):
    res.append([param_sizes[i],valid_accuracies[i],flops_list[i]])
print(res)
# Sorting the list of arrays based on the first value of each array
sorted_list = sorted(res, key=lambda x: float(x[0]))

for item in sorted_list:
    print(item)


43
43
43
[['0.583102', '93.94', '224.629900'], ['1.062910', '94.91', '225.439100'], ['0.375238', '93.17', '170.732500'], ['0.342766', '92.31', '173.113900'], ['0.493534', '93.79', '203.586100'], ['0.345358', '93.44', '175.446700'], ['1.386190', '95.11', '269.694000'], ['2.104030', '95.35', '322.648600'], ['0.332326', '93.07', '163.685500'], ['0.770734', '94.69', '195.180900'], ['1.486126', '95.1', '289.571400'], ['2.765566', '95.64', '374.468700'], ['0.755758', '94.14', '271.383100'], ['1.019998', '94.71', '218.392100'], ['2.366110', '95.26', '350.326400'], ['0.977374', '95.09', '248.164000'], ['0.833086', '94.9', '209.226300'], ['0.953902', '94.62', '233.817900'], ['1.196686', '94.96', '294.616500'], ['1.911790', '95.14', '315.616700'], ['0.399934', '92.7', '185.992900'], ['0.567550', '93.7', '221.130700'], ['0.384382', '93.12', '178.994500'], ['0.486982', '93.81', '190.658500'], ['0.824014', '94.61', '201.061500'], ['0.956350', '94.55', '203.180300'], ['2.674846', '95.36', '356.10700